In [1]:
import numpy as np
import scipy
import pandas as pd
import torch.cuda

In [ ]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'

In [2]:
#from langchain_community.document_loaders import WikipediaLoader
#docs = WikipediaLoader(query='Barack Obama', load_max_docs=2, doc_content_chars_max=100000).load()
#print(len(docs))
# print(docs[0].metadata)
# print(docs[0].page_content)
from datasets import load_dataset
ds = load_dataset('cjlovering/natural-questions-short')
class DocWrapper(object):
  def __init__(self, s):
    self.page_content = s['contexts']
    self.metadata = {}
docs = [DocWrapper(ex) for ex in ds['train']]
print(docs[:10])
print(docs[0].page_content)

c:\Users\andre\miniconda3\envs\chunking2\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


[<__main__.DocWrapper object at 0x00000184AE830BE0>, <__main__.DocWrapper object at 0x00000184AE830040>, <__main__.DocWrapper object at 0x00000184AE8302B0>, <__main__.DocWrapper object at 0x00000184AE8315D0>, <__main__.DocWrapper object at 0x00000184AD7BEAA0>, <__main__.DocWrapper object at 0x00000184AD7BE950>, <__main__.DocWrapper object at 0x00000184AD7BF0D0>, <__main__.DocWrapper object at 0x00000184AD7BCAC0>, <__main__.DocWrapper object at 0x00000184AD7BE230>, <__main__.DocWrapper object at 0x00000184AD7BC490>]
Dr. Stephanie Edwards Grey 's Anatomy character The Season 12 Promotional Photo of Jerrika Hinton as Stephanie Edwards First appearance Going , Going , Gone ( 9.01 ) September 27 , 2012 ( as recurring cast ) `` Seal Our Fate '' ( 10.01 ) September 26 , 2013 ( as series regular ) Last appearance `` Ring of Fire '' ( 13.24 ) May 18 , 2017 Created by Shonda Rhimes Portrayed by Jerrika Hinton Information Full name Stephanie Edwards Nickname ( s ) Grumpy Steph Dr. Lavender Title 

In [3]:
import os
create_chunks = True
if os.path.isfile('data/chunks.json'):
    create_chunks = False

In [4]:
from langchain_text_splitters import RecursiveCharacterTextSplitter, TokenTextSplitter, CharacterTextSplitter, NLTKTextSplitter,\
                                     SentenceTransformersTokenTextSplitter, SpacyTextSplitter
from langchain_experimental.text_splitter import SemanticChunker
from langchain_huggingface import HuggingFaceEmbeddings

if create_chunks:
    def get_splits(splitter, data):
        return [split.page_content for split in splitter.split_documents(docs)]

    rec_char_splitter = RecursiveCharacterTextSplitter(
        chunk_size=1000, chunk_overlap=200, add_start_index=True
    )
    rec_char_splitter_2 = RecursiveCharacterTextSplitter(
        chunk_size=2000, chunk_overlap=200, add_start_index=True
    )
    token_splitter = TokenTextSplitter(
        encoding_name='gpt2', chunk_size=100, chunk_overlap=0
    )
    char_splitter = CharacterTextSplitter(
        separator='\n', is_separator_regex=False
    )
    nltk_splitter = NLTKTextSplitter(
        separator='\n\n', language='english'
    )
    sentence_transformer_splitter = SentenceTransformersTokenTextSplitter(
        chunk_overlap=50, model_name='sentence-transformers/all-mpnet-base-v2', tokens_per_chunk=None
    )
    spacy_splitter = SpacyTextSplitter(
        separator='\n\n', pipeline='en_core_web_sm', max_length=1000000
    )
    semantic_chunker = SemanticChunker(
        embeddings=HuggingFaceEmbeddings(), buffer_size=1, add_start_index=True
    )
    #... add more, like the SemanticChunker, etc.                    # DONE
    #... use different parameters for these (especially chunk sizes) # TODO: How wide of a parameter space should we use? Default is 4000/200

In [5]:
if create_chunks:
    all_splits, all_ids = [], []
    splitters = [rec_char_splitter, rec_char_splitter_2, token_splitter, char_splitter, nltk_splitter, \
                sentence_transformer_splitter]
    splitters = [rec_char_splitter, token_splitter]
    for splitter in splitters:
        if splitter.__class__.__name__ != 'SemanticChunker':
            print(f'{splitter.__class__.__name__}_{splitter._chunk_size}_{splitter._chunk_overlap}')
        else:
            print(f'{splitter.__class__.__name__}')
        splits = get_splits(splitter, docs)
        all_splits.extend(splits)
        all_ids.extend([f'id_{splitter.__class__.__name__}_{ii}' for ii in range(len(splits))])
    
    df = pd.DataFrame.from_dict({'chunk': all_splits, 'id': all_ids})
    df.to_json('data/chunks.json')
else:
    df = pd.read_json('data/chunks.json')
    all_splits = list(df['chunk'].values)
    all_ids = list(df['id'].values)
    
print(all_splits[0])
print(len(all_splits))
print(all_splits[:5])
# print(all_ids)

Dr. Stephanie Edwards Grey 's Anatomy character The Season 12 Promotional Photo of Jerrika Hinton as Stephanie Edwards First appearance Going , Going , Gone ( 9.01 ) September 27 , 2012 ( as recurring cast ) `` Seal Our Fate '' ( 10.01 ) September 26 , 2013 ( as series regular ) Last appearance `` Ring of Fire '' ( 13.24 ) May 18 , 2017 Created by Shonda Rhimes Portrayed by Jerrika Hinton Information Full name Stephanie Edwards Nickname ( s ) Grumpy Steph Dr. Lavender Title M.D. Significant other ( s ) Jackson Avery Kyle Diaz ( deceased )
136863
["Dr. Stephanie Edwards Grey 's Anatomy character The Season 12 Promotional Photo of Jerrika Hinton as Stephanie Edwards First appearance Going , Going , Gone ( 9.01 ) September 27 , 2012 ( as recurring cast ) `` Seal Our Fate '' ( 10.01 ) September 26 , 2013 ( as series regular ) Last appearance `` Ring of Fire '' ( 13.24 ) May 18 , 2017 Created by Shonda Rhimes Portrayed by Jerrika Hinton Information Full name Stephanie Edwards Nickname ( s )

In [6]:
# from sklearn.feature_extraction.text import TfidfVectorizer
# from scipy import sparse


# class BM25(object):
#     def __init__(self, b=0.75, k1=1.6):
#         self.vectorizer = TfidfVectorizer(norm=None, smooth_idf=False)
#         self.b = b
#         self.k1 = k1

#     def fit(self, X):
#         ''' Fit IDF to documents X '''
#         self.vectorizer.fit(X)
#         y = super(TfidfVectorizer, self.vectorizer).transform(X)
#         self.avdl = y.sum(1).mean()

#     def transform(self, q, X):
#         ''' Calculate BM25 between query q and documents X '''
#         b, k1, avdl = self.b, self.k1, self.avdl

#         # apply CountVectorizer
#         X = super(TfidfVectorizer, self.vectorizer).transform(X)
#         len_X = X.sum(1).A1
#         q, = super(TfidfVectorizer, self.vectorizer).transform([q])
#         assert sparse.isspmatrix_csr(q)

#         # convert to csc for better column slicing
#         X = X.tocsc()[:, q.indices]
#         denom = X + (k1 * (1 - b + b * len_X / avdl))[:, None]
#         # idf(t) = log [ n / df(t) ] + 1 in sklearn, so it need to be coneverted
#         # to idf(t) = log [ n / df(t) ] with minus 1
#         idf = self.vectorizer._tfidf.idf_[None, q.indices] - 1.
#         numer = X.multiply(np.broadcast_to(idf, X.shape)) * (k1 + 1)                                                          
#         return (numer / denom).sum(1).A1


In [7]:
from fast_bm25 import BM25
my_splits = [x.split() for x in all_splits]
bm25 = BM25(my_splits)

Dropping 37 terms


In [8]:
results = bm25.get_top_n(['largest', 'city', 'in', 'Japan'], my_splits, n=10)
print(len(results), results)

10 [['The', 'automotive', 'industry', 'in', 'Japan', 'is', 'one', 'of', 'the', 'most', 'prominent', 'and', 'largest', 'industries', 'in', 'the', 'world', '.', 'Japan', 'has', 'been', 'in', 'the', 'top', 'three', 'of', 'the', 'countries', 'with', 'most', 'cars', 'manufactured', 'since', 'the', '1960s', ',', 'surpassing', 'Germany', '.', 'The', 'automotive', 'industry', 'in', 'Japan', 'rapidly', 'increased', 'from', 'the', '1970s', 'to', 'the', '1990s', '(', 'when', 'it', 'was', 'oriented', 'both', 'for', 'domestic', 'use', 'and', 'worldwide', 'export', ')', 'and', 'in', 'the', '1980s', 'and', '1990s', ',', 'overtook', 'the', 'U.S.', 'as', 'the', 'production', 'leader', 'with', 'up', 'to', '13', 'million', 'cars', 'per', 'year', 'manufactured', 'and', 'significant', 'exports', '.', 'After', 'massive', 'ramp', '-', 'up', 'by', 'China', 'in', 'the', '2000s', 'and', 'fluctuating', 'U.S.', 'output', ',', 'Japan', 'is', 'now', 'currently', 'the', 'third', 'largest', 'automotive', 'producer', 

In [9]:
q = "the common name for a modulator demodulator is"
results = bm25.get_top_n(q.split(), my_splits, n=10)
print(len(results), results)

10 [['A', 'modem', '(', 'modulator', '--', 'demodulator', ')', 'is', 'a', 'network', 'hardware', 'device', 'that', 'modulates', 'one', 'or', 'more', 'carrier', 'wave', 'signals', 'to', 'encode', 'digital', 'information', 'for', 'transmission', 'and', 'demodulates', 'signals', 'to', 'decode', 'the', 'transmitted', 'information', '.', 'The', 'goal', 'is', 'to', 'produce', 'a', 'signal', 'that', 'can', 'be', 'transmitted', 'easily', 'and', 'decoded', 'to', 'reproduce', 'the', 'original', 'digital', 'data', '.', 'Modems', 'can', 'be', 'used', 'with', 'any', 'means', 'of', 'transmitting', 'analog', 'signals', ',', 'from', 'light', '-', 'emitting', 'diodes', 'to', 'radio', '.', 'A', 'common', 'type', 'of', 'modem', 'is', 'one', 'that', 'turns', 'the', 'digital', 'data', 'of', 'a'], ['A', 'modem', '(', 'modulator', '--', 'demodulator', ')', 'is', 'a', 'network', 'hardware', 'device', 'that', 'modulates', 'one', 'or', 'more', 'carrier', 'wave', 'signals', 'to', 'encode', 'digital', 'informatio

In [10]:
# bm25 = BM25()
# bm25.fit(all_splits)

In [11]:
def retrieve_from_query(query, k):
    tokenized_query = query.split()
    retrieve = bm25.get_top_n(tokenized_query, my_splits, n=k)
    retrieved_docs = [' '.join(x) for x in retrieve]
    return retrieved_docs

In [12]:
# import chromadb
# chroma_client = chromadb.Client()
# try:
#     collection = chroma_client.create_collection(name='my_collection')
# except:
#     chroma_client.delete_collection(name='my_collection')
#     collection = chroma_client.create_collection(name='my_collection')
# collection.add(
#     documents=all_splits[:100],
#     ids=all_ids[:100]
# )

In [13]:
# results = collection.query(
#     query_texts=['where is Obama from'],
#     n_results=2 # how many results to return
# )
# print(results)

In [14]:

from torch.utils.data import DataLoader
from datasets import Dataset
from transformers import AutoTokenizer

batch_size = 8
tokenizer = AutoTokenizer.from_pretrained('facebook/opt-125m')

# Now pass the retrieval results to the LLM (basically, RAG with frozen components)

# Baseline: deduplicate retrieval results somehow

# The neural net we train:
# - For each question:
#    - Encode each chunk and output a score (how to encode?)
#    - Turn all scores over all chunks into a distribution P(d|q)
#    - For each chunk get the NLL of the correct answer as another distribution Q(d|q) (from a RAG 'open domain QA' dataset; use HF transformers to get the NLL)
#    - Minimize the KL div of those two distributions (KL_div(P||Q)) (https://arxiv.org/abs/2301.12652 - REPLUG)
# - Add loss term for the length of the sequence (number of tokens)
# - Train

# For Chroma
# def add_retrieval_results(ex):
#     ex['retrieved'] = collection.query(
#         query_texts=[ex['questions'][0]['input_text']],
#         n_results=10 # the higher the better
#     )['documents']
#     # one alternative here for speed could be to not use Chroma but some kind of sparse search like Elastic
#     return ex

# For (fast) BM25
def add_retrieval_results(ex):
    ex['retrieved'] = retrieve_from_query(ex['questions'][0]['input_text'], k=10)
    # one alternative here for speed could be to not use Chroma but some kind of sparse search like Elastic
    return ex

# Data pre-processing (tokenize and de-nesting)
def preprocess(ex):
    ex['questions'] = ex['questions'][0]['input_text']
    ex['answers'] = ex['answers'][0]['span_text']

    # tokenized_query = tokenizer(ex['questions'], padding='max_length', truncation=True, max_length=64, return_tensors='pt')
    # ex['input'] = tokenized_query

    # tokenized_docs = [tokenizer(doc, padding='max_length', truncation=True, max_length=100, return_tensors='pt') for doc in ex['retrieved']]
    # ex['tokenized_docs'] = tokenized_docs

    # tokenized_answer = tokenizer(ex['answers'], padding='max_length', truncation=True, max_length=16, return_tensors='pt')
    # ex['tokenized_answer'] = tokenized_answer
    return ex

In [ ]:
print('1')
tiny_train_dataset = Dataset.from_dict(ds['train'][:])
print('2')
tiny_train_dataset = tiny_train_dataset.map(add_retrieval_results)
print('3')
tiny_train_dataset = tiny_train_dataset.map(preprocess)
print('4')
tiny_train_dataset = tiny_train_dataset.remove_columns(['contexts', 'has_correct_context', 'name', 'id'])
tiny_train_loader = DataLoader(tiny_train_dataset, batch_size=batch_size, shuffle=True)

tiny_valid_dataset = Dataset.from_dict(ds['validation'][:])
tiny_valid_dataset = tiny_valid_dataset.map(add_retrieval_results)
tiny_valid_dataset = tiny_valid_dataset.map(preprocess)
tiny_valid_loader = DataLoader(tiny_valid_dataset, batch_size=batch_size, shuffle=True)

# train_dataset = ds['train'].map(add_retrieval_results)
# train_dataset = train_dataset.map(tokenize)
# train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
# valid_dataset = ds['valid'].map(add_retrieval_results)
# valid_dataset = valid_dataset.map(tokenize)
# valid_loader = DataLoader(valid_dataset, batch_size=batch_size)

In [ ]:
tiny_train_dataset.to_json("data/chunks_with_retrieve.json")

In [21]:
tiny_train_dataset = load_dataset("json", data_files="data/train_chunks_with_retrieve.json")['train']
print(tiny_train_dataset)
tiny_train_loader = DataLoader(tiny_train_dataset, batch_size=batch_size, shuffle=True)

Dataset({
    features: ['contexts', 'has_correct_context', 'name', 'answers', 'id', 'questions', 'retrieved'],
    num_rows: 871
})


In [ ]:
# # print(tiny_train_dataset[:8])
# first_batch = tiny_train_dataset[:8]
# for item in first_batch:
#     print(len(first_batch[item]), first_batch[item])
#     for x in first_batch[item]:
#         print(len(x), x)

In [22]:
for batch in iter(tiny_train_loader):
    # try:
        print(batch)
    # except:
    #     pass

{'contexts': ['Glass Google Glass Explorer Edition Also known as Project Glass Developer Google Manufacturer Foxconn Type Optical head - mounted display ( OHMD ) , Wearable technology Release date Developers ( US ) : February 2013 ( February 2013 ) Public ( US ) : Around 2013 Introductory price Explorer version : $1,500 USD Standard edition : Operating system Glass OS ( Google Xe Software ) CPU OMAP 4430 System on a chip , dual - core processor Memory 2 GB RAM Storage 16 GB flash memory total ( 12 GB of usable memory ) Display Prism projector , 640 × 360 pixels ( equivalent of a 25 in / 64 cm screen from 8 ft / 2.4 m away ) Sound Bone conduction transducer Input Voice command through microphone , accelerometer , gyroscope , magnetometer , ambient light sensor , proximity sensor Controller input Touchpad , MyGlass phone mobile app Camera 5 Megapixel photos 720p video Connectivity Wi - Fi 802.11 b / g , Bluetooth , micro USB Power 570 mAh Internal lithium - ion battery Weight 36 g ( 1.27

In [ ]:
print(tiny_train_dataset[0])

In [ ]:
# print(tiny_train_dataset)
# print(tiny_train_dataset['retrieved'])
# print(tiny_train_dataset['input'])
# print(tiny_train_dataset['tokenized_docs'])
# print(tiny_train_dataset[0])
# print(tiny_train_dataset['questions'])

In [ ]:
batch = next(iter(tiny_train_loader))
print(batch['questions'])
# print(batch['retrieved'][0])
# print(batch['input']['input_ids'][0])
print(batch['answers'])

In [ ]:
import torch
print((batch['retrieved']))
print([x for retr in batch['retrieved'] for x in retr])
print(tokenizer([x for retr in batch['retrieved'] for x in retr], padding=True, return_tensors='pt'))
tokenized = tokenizer([x for retr in batch['retrieved'] for x in retr], padding=True, return_tensors='pt')
print(tokenized['input_ids'].shape)
tokenized['input_ids'] = torch.reshape(tokenized['input_ids'], (len(batch['retrieved'][0]), len(batch['retrieved']), -1))
tokenized['attention_mask'] = torch.reshape(tokenized['attention_mask'], (len(batch['retrieved'][0]), len(batch['retrieved']), -1))
print(tokenized['input_ids'].shape)
# print(tokenizer(batch['retrieved']))
# print([tokenizer(x, padding=True, return_tensors='pt') for x in batch['retrieved']])
# torch.stack([tokenizer(x, padding=True, return_tensors='pt')['input_ids'] for x in batch['retrieved']])

In [ ]:
import wandb
wandb.init(
    # set the wandb project where this run will be logged
    project='chunking_experiments',

    # track hyperparameters and run metadata
    config={
    'learning_rate': 0.1,
    'architecture': 'Transformer',
    'dataset': 'NQ',
    'epochs': 10,
    }
)

In [ ]:
from transformers import AutoModelForCausalLM, AutoModel
model_id = 'facebook/opt-125m'
llm_model = AutoModelForCausalLM.from_pretrained(model_id)
tokenizer = AutoTokenizer.from_pretrained(model_id)

In [ ]:
import torch
import torch.nn as nn
class Encoder(nn.Module):
    def __init__(self, vocab_size):
        super().__init__()
        self.vocab_size = vocab_size
        self.emb_dim = 256
        self.dim_ff = 1024
        self.n_head = 4
        self.n_layers = 4
        self.embedding = nn.Embedding(num_embeddings=self.vocab_size, embedding_dim=self.emb_dim)
        self.encoding_layer = nn.TransformerEncoderLayer(d_model=self.emb_dim, nhead=self.n_head, dim_feedforward=self.dim_ff, batch_first=True)
        self.encoding_block = nn.TransformerEncoder(self.encoding_layer, num_layers=self.n_layers)

    def forward(self, input, mask):
        x = self.embedding(input)
        x = self.encoding_block(x, src_key_padding_mask=mask)
        # x = self.encoding_block(x)
        # print('before mean', x.shape, x)
        x = torch.mean(x, dim=1)
        # print('after mean', x.shape, x)
        return x

In [ ]:
import lightning as L
from tqdm import tqdm

from lightning.pytorch.demos import Transformer

# TODO by Andrew: fill in the rest from here: https://lightning.ai/docs/pytorch/stable/common/lightning_module.html
class ReplugTransformer(L.LightningModule):
    def __init__(self, vocab_size):
        super().__init__()
        # self.encoder = Transformer(vocab_size=vocab_size)
        self.query_encoder = Encoder(vocab_size) #TODO: separate for query and docs
        self.docs_encoder = Encoder(vocab_size)
        self.llm = llm_model  # LLM to get NLLs for reference distribution in KL div 
        for param in self.llm.parameters():
            param.requires_grad = False
    
    def forward(self, questions, docs):
        questions, questions_mask = questions['input_ids'], torch.logical_not(questions['attention_mask'].to(dtype=torch.bool))
        docs, docs_mask = docs['input_ids'], torch.logical_not(docs['attention_mask'].to(dtype=torch.bool))
        # Encode questions and documents
        # print('questions', questions)
        # print(len(docs), questions.shape, docs[0].shape)
        # print('docs', docs.shape, docs)
        n_examples = questions.shape[0]
        q_emb = self.query_encoder(questions, questions_mask)
        # print('q_emb', q_emb.shape, q_emb)
        # Squeeze and unsqueeze to pass batch of retrievals into encoder at once?
        # Turn B x K x L to (BK) x L
        B, K, L = docs.shape
        # print(B, K, L)
        input_docs = torch.reshape(docs, (B * K, L))
        input_docs_mask = torch.reshape(docs_mask, (B*K, -1))
        # print(input_docs.shape)
        d_embs = self.docs_encoder(input_docs, input_docs_mask)
        d_embs = torch.reshape(d_embs, (B, K, -1))
        # print(d_embs.shape)

        d_scores = torch.einsum('bij,bjk->bik', d_embs, torch.unsqueeze(q_emb, -1))
        d_scores = d_scores.squeeze()

        del input_docs, input_docs_mask, q_emb, d_embs
        torch.cuda.empty_cache()
        # print('d_scores', d_scores.shape, d_scores)

        return d_scores
    
    def expand_data(self, data, batch_size, num_docs):                   # Data: B x S
        expanded_data = torch.unsqueeze(data, 1)                         # B x 1 x S
        expanded_data = expanded_data.expand(-1, num_docs, -1)           # B x K x S
        return torch.reshape(expanded_data, (batch_size * num_docs, -1)) # BK x S

    def new_llm_pass(self, questions, docs, answers):
        # Again, reshape to put into LLM as B x ? shape
        questions, questions_mask = questions['input_ids'], torch.logical_not(questions['attention_mask'].to(dtype=torch.bool))
        docs, docs_mask = docs['input_ids'], torch.logical_not(docs['attention_mask'].to(dtype=torch.bool))
        # print(answers['attention_mask'])
        # print(answers['attention_mask'].to(dtype=torch.bool))
        # print(torch.logical_not(answers['attention_mask'].to(dtype=torch.bool)))
        answers, answers_mask = answers['input_ids'], answers['attention_mask'].to(dtype=torch.bool) # B x A
        
        # print(answers_mask)
        B, K, L = docs.shape
        docs = torch.reshape(docs, (B*K, L))                   # BK x L
        docs_mask = torch.reshape(docs_mask, (B*K, L))         # BK x L
        _, answer_length = answers.shape
        expanded_questions = self.expand_data(questions, B, K)
        expanded_questions_mask = self.expand_data(questions_mask, B, K)
        # print('expanded_questions', expanded_questions.shape, expanded_questions)
        # TODO: reconsider how the inputs are combined, right now they are just concatenated with the padding... Retokenize?
        combined_input = torch.cat([docs, expanded_questions], dim=1)      # BK x (S + L)
        combined_input_mask = torch.cat([docs_mask, expanded_questions_mask], dim=1) # BK x (S + L)
        # print('combined_input', combined_input.shape)
        expanded_answers = self.expand_data(answers, B, K)
        expanded_answers_mask = self.expand_data(answers_mask, B, K)
        # print("expanded_answers_mask", expanded_answers_mask)
        all_scores = []
        for i in range(answer_length):
            expected_tokens = expanded_answers[:, i]             # BK x 1
            expected_tokens_mask = expanded_answers_mask[:, i]   # BK x 1
            # print('expected_tokens', expected_tokens.shape, expected_tokens)
            outputs = self.llm(combined_input, combined_input_mask)                   # BK x (S+L+i) x V
            # print('outputs[logits]', outputs['logits'].shape)
            last_outputs = outputs['logits'][:, -1, :]           # BK x V
            # print('last_outputs', last_outputs.shape, last_outputs)
            scores = last_outputs[torch.arange(B*K), expected_tokens] # BK x 1
            # print('scores', scores.shape, scores)
            # print("expected_tokens_mask", expected_tokens_mask)
            scores = torch.where(expected_tokens_mask == 1, scores, torch.nan)
            # print('scores', scores.shape, scores)
            all_scores.append(scores)

            combined_input = torch.cat([combined_input, torch.unsqueeze(expected_tokens, 1)], dim=1) #BK x (S + L + i)
            combined_input_mask = torch.cat([combined_input_mask, torch.unsqueeze(expected_tokens_mask, 1)], dim=1)
            del expected_tokens, expected_tokens_mask, outputs, last_outputs
            torch.cuda.empty_cache()
        all_scores = torch.stack([x for x in all_scores], dim=1)
        # print('all_scores', all_scores.shape, all_scores)
        all_scores = all_scores.reshape(B, K, -1)
        # print('all_scores', all_scores.shape, all_scores)
        all_scores = torch.nanmean(all_scores, dim=-1)
        # print('all_scores', all_scores.shape, all_scores)
        return all_scores

    def training_step(self, batch, batch_idx):
        # TODO: Make this actually work with the dataset constructed above
        # Pre-Process data (moved from above in order to batch tokenize for efficiency)
        questions = batch['questions']
        docs = batch['retrieved']
        answers = batch['answers']
        tokenized_questions = tokenizer(questions, padding=True, return_tensors='pt').to(device)
        tokenized_docs = tokenizer([x for retr in docs for x in retr], padding='max_length', truncation=True, max_length=100, return_tensors='pt').to(device)
        tokenized_docs['input_ids'] = torch.reshape(tokenized_docs['input_ids'], (len(docs[0]), len(docs), -1))
        tokenized_docs['attention_mask'] = torch.reshape(tokenized_docs['attention_mask'], (len(batch['retrieved'][0]), len(batch['retrieved']), -1))
        tokenized_answers = tokenizer(answers, padding=True, return_tensors='pt').to(device)

        self.query_encoder = self.query_encoder.to(device)
        self.docs_encoder = self.docs_encoder.to(device)
        self.llm = self.llm.to(device)
        
        # Normalize the retrieval scores from the forward pass
        # TODO: Apply the masks in the scoring process - currently no masks but still converges on single batch

        reranker_output = self(tokenized_questions, tokenized_docs)  # output is retrieval scores?
        rerank_dist = torch.nn.functional.log_softmax(reranker_output, dim=1)
        
        # Run an LLM to get the NLLs - NLLs or is it just the logits??
        llm_output = self.new_llm_pass(tokenized_questions, tokenized_docs, tokenized_answers)
        llm_dist = torch.nn.functional.softmax(llm_output, dim=1)

        print('rerank', rerank_dist.shape, rerank_dist)
        # print(rerank_dist)
        print('llm', llm_dist.shape, llm_dist)
        # print(llm_dist)

        # Compute loss = kldiv(scores, nlls)
        lossfn = torch.nn.KLDivLoss(reduction='batchmean')
        loss = lossfn(rerank_dist, llm_dist) # see docs for notation https://pytorch.org/docs/stable/generated/torch.nn.KLDivLoss.html
        print(loss)
        self.log('train_loss', loss.item(), on_step=True, on_epoch=True, prog_bar=True, logger=True, batch_size=batch_size)
        wandb.log({'train_loss': loss.item()})
        del reranker_output, rerank_dist, llm_output, llm_dist, lossfn
        return loss

    def configure_optimizers(self):
        return torch.optim.AdamW([self.query_encoder.parameters(), self.docs_encoder.parameters()], lr=1e-4)

model = ReplugTransformer(vocab_size=tokenizer.vocab_size)
trainer = L.Trainer()
trainer.fit(model, tiny_train_loader, tiny_valid_loader)

In [ ]:
#for batch in ds['train']:
#  batch_scores = net(batch) # Bx1 float
#  retrieval_scores = F.softmax(batch_scores)
#  nll_scores = llm(batch).mean() # Bx1 float
#  loss = kldiv(batch_scores, nll_scores)
#  # TODO: loss += weight_coeff * sum([len(x) for x in batch])
#  loss.backward()

# Process:
# - Retrieve with high n_results
# - Rerank using the above neural net
# - Take the top-k from that reranker
# - Give to LLM
# - Evaluate

# Once the above actually works:
# - Add additional deduplication steps?
# - Add a diversity term to the loss?
# - Add metadata to the chunk (e.g. prefix 'TokenTextSplitter' to each such chunk for the net() call, NOT the llm() call)


# Document score side:
# Input: BxS
# After retrieval: (BxS, BxKxL) (assume tokenized)
# After encoding: (BxSxE -> BxE), (BxKxE) (where E is embedding/hidden dim, separate encoders)
# After scoring: BxK (do bmm/einsum to get this)
# After normalize: BxK (logsoftmax, make sure you don't do double log)

# NLL score side:
# Input: BxS
# After encoding: Bx(S+L) -> Bx(Correct Answer)xV -> select logit of correct token, take mean -> Bx1

# 'Context: The largest city in Japan is Tokyo. Question: What is the largest city in Japan? Answer: ' -> what is the logit for Tokyo?
# Autoregressively generate for max_length_of_correct_answers_in_batch, giving you some matrix BxM,
# zero out all the components that you don't need (ie if the correct answer was 1 token, all the other tokens you can zero out),
# then take the mean of the non-zero elements to get Bx1 NLL tensor

# ^ TODO: double check that this is how Replug does it

# After loss: Bx1 (kldiv)

# Experimental protocol:
# 1. Validate that you get the above shapes
# 2. Print the BxK scores over time, make sure they change
# 3. 'Spike' the retrievals with 7 bad examples and 1 correct one, make sure the mass shifts to the correct one
# 4. Make sure train loss goes down (first on the spiked one, then on single batch, then all batches)
# 5. Run with fast BM25
